# Match Glucose Data

In [2]:
# Import cell (refined)
import numpy as np
import pandas as pd
import scipy.special as sp
import scipy.optimize
from scipy.optimize import curve_fit
import scipy.integrate
from scipy.integrate import odeint

import panel as pn

import bokeh.io
import bokeh.plotting


import bebi103
import bokeh_catplot

import cmdstanpy
import arviz as az



bokeh.io.output_notebook()
pn.extension()
 

Loading BokehJS ...

In [13]:
df_glu = pd.read_csv('../bowie_data_glucose_2.csv')
x0_glu = float(df_glu.columns[0])
x1_glu = float(df_glu.columns[1])
data_glu = [x0_glu, x1_glu]
new_row_glu = pd.DataFrame({'x':x0_glu, 'y':x1_glu}, index =[0])
df_col_glu = df_glu
df_col_glu.columns = ['x', 'y']
df_new_glu = pd.concat([new_row_glu, df_col_glu], ignore_index=True)

In [14]:
p_glu = bokeh.plotting.figure(width = 450, height = 350,
        
                          title = 'Bowie Lab Glucose Experimental Data',
                         y_axis_label = 'Glucose consumed (mM)',
                         x_axis_label = 'Time (hrs)')
p_glu.circle(df_new_glu['x'].values, df_new_glu['y'].values)
#p_glu.circle(x_add, y_add, color = 'orange', size = 7)
bokeh.io.show(p_glu)

## Model 1: Time between glucose binding to hexokinase is exponentially distributed

Glucose binding is caused by a poisson process, and the binding occurs with an average rate of $\beta$, and there is no memory of previous binding events. Then, the time between each binding event is exponentially distributed.

I want time in between binding of glucose to hexokinase. How can I get that? 

In [16]:
df_new_glu = df_new_glu.rename(columns = {'x': 'glucose consumed (mM)', 'y': 'time (hrs)'})
df_new_glu.head()

glucose consumed (mM)  time (hrs)
0               0.449080    2.564103
1               1.335651   17.948718
2               2.225120   30.769231
3               2.656816   48.717949
4               3.992467   66.666667

In [20]:
gluc_cons = df_new_glu['glucose consumed (mM)'].values
time_hrs = df_new_glu['time (hrs)'].values

In [17]:
# Convert from mM to molecules
df_new_glu['glucose molecules consumed'] = df_new_glu['glucose consumed (mM)']*10e6
df_new_glu.head()

glucose consumed (mM)  time (hrs)  glucose molecules consumed
0               0.449080    2.564103                4.490801e+06
1               1.335651   17.948718                1.335651e+07
2               2.225120   30.769231                2.225120e+07
3               2.656816   48.717949                2.656816e+07
4               3.992467   66.666667                3.992467e+07

In [18]:
gluc_mols_cons = df_new_glu['glucose molecules consumed'].values

In [21]:
# Find in x time, y more molecules bound
gluc_rates = []
time_diffs = []
for i,conc in enumerate(gluc_mols_cons):
    if i+1 == len(gluc_mols_cons):
        break
    gluc_rates.append(gluc_mols_cons[i+1] - gluc_mols_cons[i])
    time_diffs.append(time_hrs[i+1] - time_hrs[i])

In [22]:
time_diffs.remove(time_diffs[5]) # get rid of neg number
gluc_rates.remove(gluc_rates[5])

In [23]:
time_diffs

[15.384615384615415,
 12.820512820512821,
 17.948717948717952,
 17.948717948717956,
 25.641025641025635,
 25.641025641025635,
 20.512820512820582,
 12.82051282051279,
 12.820512820512818,
 17.948717948717928,
 15.384615384615415,
 10.256410256410248,
 17.948717948717956,
 15.384615384615415,
 12.82051282051279,
 12.820512820512846,
 7.692307692307679,
 10.25641025641022,
 10.256410256410334,
 12.820512820512704,
 7.692307692307736,
 5.128205128205195,
 10.25641025641022,
 7.692307692307679,
 5.128205128205138,
 5.128205128205138,
 0.0,
 5.128205128205138,
 5.128205128205082,
 7.692307692307679]

Now I have in x time, y more molecules are bound. I want in x/y time, 1 more molecule is bound

In [24]:
inter_times = [time_diffs[i]/gluc_rates[i] for i,_ in enumerate(gluc_rates)]

In [25]:
for i,_ in enumerate(inter_times):
    print(i,_)

0 1.735294117647061e-06
1 1.4413680781758897e-06
2 4.157718120805407e-06
3 1.3438177874186534e-06
4 1.441368078175898e-06
5 1.149350649350646e-06
6 1.1493506493506591e-06
7 1.4413680781758755e-06
8 7.148626817447509e-07
9 1.004051863857372e-06
10 1.149350649350654e-06
11 5.709677419354839e-07
12 8.014230271668836e-07
13 6.860465116279113e-07
14 4.7529538131041645e-07
15 7.148626817447502e-07
16 3.416988416988406e-07
17 3.7982832618025607e-07
18 3.798283261802611e-07
19 5.709677419354805e-07
20 1.895074946466825e-07
21 1.623853211009187e-07
22 3.2536764705882236e-07
23 2.1325301204819228e-07
24 1.2624821683309626e-07
25 1.420545746388444e-07
26 0.0
27 1.2624821683309552e-07
28 1.4205457463884284e-07
29 2.845659163987143e-07


In [26]:
inter_times.remove(inter_times[26])

In [27]:
gluc_one_m = np.ones(len(inter_times))

I think the inter_times values are exponentially distributed

In [28]:
N = 1000

In [29]:
data = inter_times

In [ ]:
sm_exp_prior_pred = cmdstanpy.CmdStanModel(stan_file = "exponential_prior.stan")

In [ ]:
cmdstanpy.CmdStanModel.sample?

In [ ]:
print(sm_exp_prior_pred.code())

In [ ]:
data_exp_prior = {
    "N": N,
    "beta_mu": 0,
    "beta_sigma": 0.55
}

samples_exp_prior = sm_exp_prior_pred.sample(data=data_exp_prior,
                                             iter_sampling=1000, fixed_param=True)

samples_exp_prior = az.from_cmdstanpy(posterior=samples_exp_prior, 
                                      prior=samples_exp_prior, prior_predictive=['t'])

In [ ]:
bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        samples_exp_prior.prior_predictive["t"], x_axis_label="time to catastrophe (s)", title = 'Exponential Distribution Model'
    )
)

In [ ]:
print("Number of negative sample times: ", (samples_exp_prior.prior_predictive['t'] < 0).values.sum())

## Parameter estimates + posterior predictive checks

In [ ]:
N_ppc = 200
data_post = {
    "N": len(data),
    "t": data,
    "N_ppc": N_ppc
}

In [ ]:
sm_exp_post = cmdstanpy.CmdStanModel(stan_file = "exponential_posterior.stan")

print(sm_exp_post.code())

In [ ]:
samples_exp_post = sm_exp_post.sample(data=data_post, iter_sampling=1000, chains=4)

samples_exp_post = az.from_cmdstanpy(posterior=samples_exp_post, posterior_predictive=['t_ppc'])

In [ ]:
df_mcmc_exp = samples_exp_post.posterior.to_dataframe()
df_mcmc_exp.mean()

In [ ]:
import bokeh_catplot

In [ ]:
bokeh.io.show(bokeh_catplot.ecdf(df_mcmc_exp, val='beta_'))

In [ ]:
t_ppc_exp = samples_exp_post.posterior_predictive['t_ppc'].stack(
    {"sample": ("chain", "draw")}
).transpose("sample", "t_ppc_dim_0")

bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        t_ppc_exp,
        percentiles=[30, 50, 70, 99],
        data=data,
        x_axis_label='time to catastrophe (s)'
    )
)

### AHHH
Ok maybe this isn't the way we should be doing. They had inter-arrival times. We can try to look at glucose consumed / time = approximate as normal?

I want to estimate the rate data - want to know the rate of glucose consumption. Model that as a normal distribution plz.

In [112]:
df_new_glu.head()

glucose consumed (mM)  time (hrs)  glucose molecules consumed
0               0.449080    2.564103                4.490801e+06
1               1.335651   17.948718                1.335651e+07
2               2.225120   30.769231                2.225120e+07
3               2.656816   48.717949                2.656816e+07
4               3.992467   66.666667                3.992467e+07

Let's compute the rates again

In [113]:
gluc_vals = df_new_glu['glucose consumed (mM)'].values
times = df_new_glu['time (hrs)'].values

In [116]:
glu_rates = []
for i,val in enumerate(gluc_vals):
    if i+1 == len(gluc_vals):
        break
    glu_rates.append((gluc_vals[i+1]- gluc_vals[i]) /(times[i+1] - times[i]))


/Users/ankitaroychoudhury/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:5: RuntimeWarning: divide by zero encountered in double_scalars
  """


In [117]:
glu_rates

[0.05762711864406772,
 0.06937853107344663,
 0.02405165456012892,
 0.07441485068603722,
 0.06937853107344623,
 0.04293785310734444,
 0.08700564971751436,
 0.0870056497175134,
 0.06937853107344735,
 0.1398870056497172,
 0.09959644874899132,
 0.08700564971751384,
 0.17514124293785313,
 0.12477804681194492,
 0.14576271186440584,
 0.2103954802259899,
 0.13988700564971746,
 0.2926553672316389,
 0.26327683615819314,
 0.26327683615818986,
 0.17514124293785388,
 0.5276836158192052,
 0.615819209039543,
 0.3073446327683629,
 0.4689265536723171,
 0.7920903954802224,
 0.7039548022598862,
 inf,
 0.7920903954802265,
 0.7039548022598939,
 0.3514124293785304]

In [118]:
glu_rates.remove(rates[27])


Now, use the rates as what you pass into the function

In [34]:
# prior exponential

In [35]:
N = 1000
data = rates
sm_exp_prior_pred = cmdstanpy.CmdStanModel(stan_file = "exponential_prior.stan")

data_exp_prior = {
    "N": N,
    "beta_mu": 0,
    "beta_sigma": 0.55
}

samples_exp_prior = sm_exp_prior_pred.sample(data=data_exp_prior, 
                                             iter_sampling=1000, fixed_param=True)

samples_exp_prior = az.from_cmdstanpy(posterior=samples_exp_prior, 
                                      prior=samples_exp_prior, prior_predictive=['t'])
bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        samples_exp_prior.prior_predictive["t"], x_axis_label="time to catastrophe (s)", title = 'Exponential Distribution Model'
    )
)

INFO:cmdstanpy:compiling stan program, exe file: /Users/ankitaroychoudhury/Documents/MURRAY/simulations/bowie_data/stan_glucose/exponential_prior
INFO:cmdstanpy:compiler options: stanc_options=None, cpp_options=None


KeyboardInterrupt: 

In [ ]:
N_ppc = 200
data_post = {
    "N": len(data),
    "k": data,
    "N_ppc": N_ppc
}

sm_exp_post = cmdstanpy.CmdStanModel(stan_file = "exponential_posterior.stan")

df_mcmc_exp = samples_exp_post.posterior.to_dataframe()
df_mcmc_exp.mean()
bokeh.io.show(bokeh_catplot.ecdf(df_mcmc_exp, val='beta_'))

In [ ]:
t_ppc_exp = samples_exp_post.posterior_predictive['t_ppc'].stack(
    {"sample": ("chain", "draw")}
).transpose("sample", "t_ppc_dim_0")

bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        t_ppc_exp,
        percentiles=[30, 50, 70, 99],
        data=data,
        x_axis_label='time to catastrophe (s)'
    )
)

## Test: The rates follow a normal distribution

prior predictive check

nevermind idrk what i'm doing: posterior predictive check

In [ ]:
cmdstandpy.CmdStanModel?

In [50]:
bebi103.stan.clean_cmdstan()


In [159]:
sm = cmdstanpy.CmdStanModel(stan_file='normal_posterior.stan')

INFO:cmdstanpy:compiling stan program, exe file: /Users/ankitaroychoudhury/Documents/MURRAY/simulations/bowie_data/stan_glucose/normal_posterior
INFO:cmdstanpy:compiler options: stanc_options=None, cpp_options=None
INFO:cmdstanpy:compiled model file: /Users/ankitaroychoudhury/Documents/MURRAY/simulations/bowie_data/stan_glucose/normal_posterior


In [163]:
data = glu_rates
N_ppc = 200
data_dict = {
    'N': len(data),
    'k': data,
    "N_ppc":N_ppc
}

In [164]:
samples_exp_post = sm.sample(data=data_dict, iter_sampling=1000, chains=4)

samples_exp_post = az.from_cmdstanpy(posterior=samples_exp_post, posterior_predictive=['k_ppc'])

INFO:cmdstanpy:start chain 1
INFO:cmdstanpy:start chain 2
INFO:cmdstanpy:finish chain 1
INFO:cmdstanpy:finish chain 2
INFO:cmdstanpy:start chain 3
INFO:cmdstanpy:start chain 4
INFO:cmdstanpy:finish chain 3
INFO:cmdstanpy:finish chain 4


get the parameter estimate for mu, sigma

In [165]:
df_mcmc_exp = samples_exp_post.posterior.to_dataframe()
df_mcmc_exp.mean()

mu       0.257643
sigma    0.247210
dtype: float64

In [166]:
from bokeh.layouts import row

visualize posterior distribution of mu and sigma

In [167]:
mu_ecdf = bokeh_catplot.ecdf(df_mcmc_exp, val='mu', title = 'mu')
sigma_ecdf = bokeh_catplot.ecdf(df_mcmc_exp, val='sigma', title = 'sigma')
bokeh.io.show(row(mu_ecdf, sigma_ecdf))

In [168]:
k_ppc_exp

<xarray.DataArray 'k_ppc' (sample: 4000, k_ppc_dim_0: 200)>
array([[ -4.84458  ,  14.5106   ,  -7.0462   , ...,  -6.88429  ,
        -23.8379   ,  11.5794   ],
       [ 17.486    ,   0.0453009,  -1.42137  , ..., -21.9587   ,
          2.33978  ,  -0.656511 ],
       [  7.06225  ,  -4.40862  ,  -6.77632  , ...,  -4.38905  ,
          6.34685  ,  -3.5993   ],
       ...,
       [ -0.837758 , -41.3905   ,   0.654996 , ...,  26.2062   ,
         -5.09025  ,   8.59984  ],
       [-10.9879   ,  -4.78682  ,  -5.5991   , ...,  21.2978   ,
          8.3179   ,  12.4053   ],
       [ 12.5511   ,  -6.63334  , -16.9094   , ...,  -4.57409  ,
          5.75034  ,  -5.15975  ]])
Coordinates:
  * k_ppc_dim_0  (k_ppc_dim_0) int64 0 1 2 3 4 5 6 ... 194 195 196 197 198 199
  * sample       (sample) MultiIndex
  - chain        (sample) int64 0 0 0 0 0 0 0 0 0 0 0 ... 3 3 3 3 3 3 3 3 3 3 3
  - draw         (sample) int64 0 1 2 3 4 5 6 7 ... 993 994 995 996 997 998 999

In [171]:
k_ppc_exp = samples_exp_post.posterior_predictive['k_ppc'].stack(
    {"sample": ("chain", "draw")}
).transpose("sample", "k_ppc_dim_0")

bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        k_ppc_exp,
        percentiles=[30, 50, 70, 99],
        data=data,
        x_axis_label='glucose binding rates (mM/hr)',
        title = 'Glucose Binding Rates as a Normal Distribution'
    )
)

## DO THIS WITH SOME MORE DATA GLUCOSE
## ALSO DO THIS WITH ONLY 5 points

### Try k ~ lognormal(mu, sigma)

In [68]:
sm_log = cmdstanpy.CmdStanModel(stan_file='lognormal_posterior.stan')

INFO:cmdstanpy:compiling stan program, exe file: /Users/ankitaroychoudhury/Documents/MURRAY/simulations/bowie_data/stan_glucose/lognormal_posterior
INFO:cmdstanpy:compiler options: stanc_options=None, cpp_options=None
INFO:cmdstanpy:compiled model file: /Users/ankitaroychoudhury/Documents/MURRAY/simulations/bowie_data/stan_glucose/lognormal_posterior


In [69]:
data = rates
N_ppc = 200
data_dict = {
    'N': len(data),
    'k': data,
    "N_ppc":N_ppc
}

In [70]:
samples_exp_post = sm_log.sample(data=data_dict, iter_sampling=1000, chains=4)

samples_exp_post = az.from_cmdstanpy(posterior=samples_exp_post, posterior_predictive=['k_ppc'])

INFO:cmdstanpy:start chain 1
INFO:cmdstanpy:start chain 2
INFO:cmdstanpy:finish chain 1
INFO:cmdstanpy:start chain 3
INFO:cmdstanpy:finish chain 2
INFO:cmdstanpy:start chain 4
INFO:cmdstanpy:finish chain 3
INFO:cmdstanpy:finish chain 4


In [71]:
df_mcmc_exp = samples_exp_post.posterior.to_dataframe()
df_mcmc_exp.mean()

mu       0.000007
sigma    2.015203
dtype: float64

In [72]:
mu_ecdf = bokeh_catplot.ecdf(df_mcmc_exp, val='mu', title = 'mu')
sigma_ecdf = bokeh_catplot.ecdf(df_mcmc_exp, val='sigma', title = 'sigma')
bokeh.io.show(row(mu_ecdf, sigma_ecdf))

In [73]:
k_ppc_exp = samples_exp_post.posterior_predictive['k_ppc'].stack(
    {"sample": ("chain", "draw")}
).transpose("sample", "k_ppc_dim_0")

bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        k_ppc_exp,
        percentiles=[30, 50, 70, 99],
        data=data,
        x_axis_label='binding rates'
    )
)

this ain't it. Use normal - figure out why it goes lower later - maybe can omit but not great

## Do it with 5 data points

In [101]:
times = [0.0003611738148947552, 
5.882799097065458, 
24.063205417607207, 
47.871060948081265, 
71.8584198645598]
gluc_vals = [0,93.90519187358922,242.88939051918737,323.2505643340858,
         354.85327313769756]

In [102]:
rates = []
for i, val in enumerate(gluc_vals):
    if i+1 == len(gluc_vals):
        break
    rates.append((gluc_vals[i+1] - gluc_vals[i]) / (times[i+1] - times[i]))


In [103]:
rates

[15.963651992386577, 8.194767268609574, 3.3754058072150235, 1.3174734623202595]

In [104]:
sm = cmdstanpy.CmdStanModel(stan_file='normal_posterior.stan')

INFO:cmdstanpy:found newer exe file, not recompiling
INFO:cmdstanpy:compiled model file: /Users/ankitaroychoudhury/Documents/MURRAY/simulations/bowie_data/stan_glucose/normal_posterior


In [105]:
data = rates
N_ppc = 200
data_dict = {
    'N': len(data),
    'k': data,
    "N_ppc":N_ppc
}

In [106]:
samples_exp_post = sm.sample(data=data_dict, iter_sampling=1000, chains=4)

samples_exp_post = az.from_cmdstanpy(posterior=samples_exp_post, posterior_predictive=['k_ppc'])

INFO:cmdstanpy:start chain 1
INFO:cmdstanpy:start chain 2
INFO:cmdstanpy:finish chain 1
INFO:cmdstanpy:finish chain 2
INFO:cmdstanpy:start chain 3
INFO:cmdstanpy:start chain 4
INFO:cmdstanpy:finish chain 3
INFO:cmdstanpy:finish chain 4


In [107]:
df_mcmc_exp = samples_exp_post.posterior.to_dataframe()
df_mcmc_exp.mean()

mu        0.006509
sigma    11.131670
dtype: float64

In [108]:
mu_ecdf = bokeh_catplot.ecdf(df_mcmc_exp, val='mu', title = 'mu')
sigma_ecdf = bokeh_catplot.ecdf(df_mcmc_exp, val='sigma', title = 'sigma')
bokeh.io.show(row(mu_ecdf, sigma_ecdf))

In [109]:
k_ppc_exp = samples_exp_post.posterior_predictive['k_ppc'].stack(
    {"sample": ("chain", "draw")}
).transpose("sample", "k_ppc_dim_0")

bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        k_ppc_exp,
        percentiles=[30, 50, 70, 99],
        data=data,
        x_axis_label='Glucose consumption rates (mM/hr)',
        title = 'Glucose Consumption Rates as a Normal Distribution (5 data points)'
    )
)

# Try Gamma distribution!

In [110]:
sm_gamma_post = cmdstanpy.CmdStanModel(stan_file = "gamma_posterior.stan")

print(sm_gamma_post.code())

INFO:cmdstanpy:compiling stan program, exe file: /Users/ankitaroychoudhury/Documents/MURRAY/simulations/bowie_data/stan_glucose/gamma_posterior
INFO:cmdstanpy:compiler options: stanc_options=None, cpp_options=None
INFO:cmdstanpy:compiled model file: /Users/ankitaroychoudhury/Documents/MURRAY/simulations/bowie_data/stan_glucose/gamma_posterior


data {
  int<lower=0> N;
  real k[N];
  int<lower=0> N_ppc;
}

parameters {
  real<lower=0> alpha;
  real<lower=0> beta;
}

model {

    //Priors
  alpha ~ lognormal(0, 2);
  beta ~ lognormal(0,3);
  //Likelihood
  
  //k ~ normal(0, 1);
  
  k ~ gamma(alpha, beta);
}

generated quantities{

    real k_ppc[N_ppc];
    for (i in 1:N_ppc){
        k_ppc[i] = gamma_rng(alpha, beta);
        }
}



In [134]:
data = glu_rates
N_ppc = 200
data_gamma = {
    "N": len(data),
    "k": data,
    "N_ppc": N_ppc
}


In [135]:
samples_gamma_post = sm_gamma_post.sample(data=data_gamma, iter_sampling=1000, chains=4)

samples_gamma_post = az.from_cmdstanpy(posterior=samples_gamma_post, posterior_predictive=['k_ppc'])

INFO:cmdstanpy:start chain 1
INFO:cmdstanpy:start chain 2
INFO:cmdstanpy:finish chain 1
INFO:cmdstanpy:start chain 3
INFO:cmdstanpy:finish chain 2
INFO:cmdstanpy:start chain 4
INFO:cmdstanpy:finish chain 3
INFO:cmdstanpy:finish chain 4


parameter estimates for alpha and beta

In [136]:
df_mcmc_gamma = samples_gamma_post.posterior.to_dataframe()
df_mcmc_gamma.mean()

alpha    1.348637
beta     5.073315
dtype: float64

In [139]:
bokeh.io.show(bebi103.viz.corner(samples_gamma_post, xtick_label_orientation=np.pi / 4))

In [140]:
samples_gamma_post

Inference data with groups:
	> posterior
	> sample_stats
	> posterior_predictive

In [142]:
k_ppc_gamma = samples_gamma_post.posterior_predictive['k_ppc'].stack(
    {"sample": ("chain", "draw")}
).transpose("sample", "k_ppc_dim_0")

bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        k_ppc_gamma,
        percentiles=[30, 50, 70, 99],
        data=data,
        x_axis_label='glucose binding rates (mM/hr)',
        title = 'Glucose Binding Rates as a Gamma Distribution'
    )
)

## Half normal glucose

In [155]:
sm_halfnorm_post = cmdstanpy.CmdStanModel(stan_file = "halfnormal_posterior.stan")

print(sm_gamma_post.code())

INFO:cmdstanpy:compiling stan program, exe file: /Users/ankitaroychoudhury/Documents/MURRAY/simulations/bowie_data/stan_glucose/halfnormal_posterior
INFO:cmdstanpy:compiler options: stanc_options=None, cpp_options=None
INFO:cmdstanpy:compiled model file: /Users/ankitaroychoudhury/Documents/MURRAY/simulations/bowie_data/stan_glucose/halfnormal_posterior


data {
  int<lower=0> N;
  real k[N];
  int<lower=0> N_ppc;
}

parameters {
  real<lower=0> alpha;
  real<lower=0> beta;
}

model {

    //Priors
  alpha ~ lognormal(0, 2);
  beta ~ lognormal(0,3);
  //Likelihood
  
  //k ~ normal(0, 1);
  
  k ~ gamma(alpha, beta);
}

generated quantities{

    real k_ppc[N_ppc];
    for (i in 1:N_ppc){
        k_ppc[i] = gamma_rng(alpha, beta);
        }
}



In [156]:
data = glu_rates
N_ppc = 200
data_halfnorm = {
    "N": len(data),
    "k": data,
    "N_ppc": N_ppc
}
samples_halfnorm_post = sm_halfnorm_post.sample(data=data_halfnorm, iter_sampling=1000, chains=4)

samples_halfnorm_post = az.from_cmdstanpy(posterior=samples_halfnorm_post, posterior_predictive=['k_ppc'])
df_mcmc_halfnorm = samples_halfnorm_post.posterior.to_dataframe()
df_mcmc_halfnorm.mean()

INFO:cmdstanpy:start chain 1
INFO:cmdstanpy:start chain 2
INFO:cmdstanpy:finish chain 1
INFO:cmdstanpy:start chain 3
INFO:cmdstanpy:finish chain 2
INFO:cmdstanpy:start chain 4
INFO:cmdstanpy:finish chain 3
INFO:cmdstanpy:finish chain 4


mu       0.255441
sigma    0.248098
dtype: float64

In [157]:
k_ppc_halfnorm = samples_halfnorm_post.posterior_predictive['k_ppc'].stack(
    {"sample": ("chain", "draw")}
).transpose("sample", "k_ppc_dim_0")

bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        k_ppc_halfnorm,
        percentiles=[30, 50, 70, 99],
        data=data,
        x_axis_label='glucose binding rates (mM/hr)',
        title = 'Glucose Binding Rates as a Half-Normal Distribution'
    )
)

## Maybe troubleshoot later

## Model comparison - normal and gamma for glucose

In [172]:
az.compare({'normal': samples_exp_post, 'gamma': samples_gamma_post}, ic='waic')


TypeError: log likelihood not found in inference data object

# Glucose, NORMAL, all data, with log likelihood

In [181]:
sm_norm_postlog = cmdstanpy.CmdStanModel(stan_file = "normal_loglik_posterior.stan")

print(sm_norm_postlog.code())

INFO:cmdstanpy:found newer exe file, not recompiling
INFO:cmdstanpy:compiled model file: /Users/ankitaroychoudhury/Documents/MURRAY/simulations/bowie_data/stan_glucose/normal_loglik_posterior


data {
  int<lower=0> N;
  real k[N];
  int N_ppc;
}

parameters {
  real<lower=0> mu;
  real<lower=0> sigma;
}

model {

    //Priors
  mu ~ lognormal(0, 2);
  sigma ~ lognormal(2,3);
  //Likelihood
  
  //k ~ normal(0, 1);
  
  k ~ normal(mu, sigma);
}

generated quantities{

    real k_ppc[N_ppc];
    real log_lik[N];
    
    for (i in 1:N_ppc){
        k_ppc[i] = normal_rng(mu, sigma);
        }
        
    for (i in 1:N) {
        log_lik[i] = normal_lpdf(k[i] | mu, sigma);
        }
}




In [189]:
data = glu_rates
N_ppc = 200
data_norm = {
    "N": len(data),
    "k": data,
    "N_ppc": N_ppc
}
samples_norm_postlog = sm_norm_postlog.sample(data=data_norm, iter_sampling=1000, chains=4)

samples_norm_postlog = az.from_cmdstanpy(posterior=samples_norm_postlog, posterior_predictive=['k_ppc'],
                                        log_likelihood = 'log_lik')
df_mcmc_norm_log = samples_norm_postlog.posterior.to_dataframe()
df_mcmc_norm_log.mean()

INFO:cmdstanpy:start chain 1
INFO:cmdstanpy:start chain 2
INFO:cmdstanpy:finish chain 2
INFO:cmdstanpy:finish chain 1
INFO:cmdstanpy:start chain 3
INFO:cmdstanpy:start chain 4
INFO:cmdstanpy:finish chain 3
INFO:cmdstanpy:finish chain 4


mu       0.256064
sigma    0.248727
dtype: float64

In [196]:
k_ppc_normlog = samples_norm_postlog.posterior_predictive['k_ppc'].stack(
    {"sample": ("chain", "draw")}
).transpose("sample", "k_ppc_dim_0")

bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        k_ppc_normlog,
        percentiles=[30, 50, 70, 99],
        data=data,
        x_axis_label='glucose binding rates (mM/hr)',
        title = 'Glucose Binding Rates as a Normal Distribution'
    )
)

In [190]:
az.waic(samples_norm_postlog)


/Users/ankitaroychoudhury/opt/anaconda3/lib/python3.7/site-packages/arviz/stats/stats.py:1210: UserWarning: For one or more samples the posterior variance of the log predictive densities exceeds 0.4. This could be indication of WAIC starting to fail. 
See http://arxiv.org/abs/1507.04544 for details
  "For one or more samples the posterior variance of the log predictive "


Computed from 4000 by 30 log-likelihood matrix

          Estimate       SE
elpd_waic    -1.65     4.03
p_waic        2.01        -

There has been a warning during the calculation. Please check the results.

# Glucose, GAMMA, all data, with log likelihood

In [180]:
sm_gamma_post = cmdstanpy.CmdStanModel(stan_file = "gamma_posteriorlog.stan")

print(sm_gamma_post.code())

INFO:cmdstanpy:found newer exe file, not recompiling
INFO:cmdstanpy:compiled model file: /Users/ankitaroychoudhury/Documents/MURRAY/simulations/bowie_data/stan_glucose/gamma_posteriorlog


data {
  int<lower=0> N;
  real k[N];
  int<lower=0> N_ppc;
}

parameters {
  real<lower=0> alpha;
  real<lower=0> beta;
}

model {

    //Priors
  alpha ~ lognormal(0, 2);
  beta ~ lognormal(0,3);
  //Likelihood
  
  //k ~ normal(0, 1);
  
  k ~ gamma(alpha, beta);
}

generated quantities{

    real k_ppc[N_ppc];
    real log_lik[N];


    for (i in 1:N_ppc){
        k_ppc[i] = gamma_rng(alpha, beta);
        }
        
    for (i in 1:N) {
        log_lik[i] = gamma_lpdf(k[i] | alpha, beta);
        }
}



In [191]:
data = glu_rates
N_ppc = 200
data_norm = {
    "N": len(data),
    "k": data,
    "N_ppc": N_ppc
}
samples_gamma_post = sm_gamma_post.sample(data=data_norm, iter_sampling=1000, chains=4)

samples_gamma_post = az.from_cmdstanpy(posterior=samples_gamma_post, posterior_predictive=['k_ppc'],
                                      log_likelihood ='log_lik')
df_mcmc_gamma_post = samples_gamma_post.posterior.to_dataframe()
df_mcmc_gamma_post.mean()

INFO:cmdstanpy:start chain 1
INFO:cmdstanpy:start chain 2
INFO:cmdstanpy:finish chain 2
INFO:cmdstanpy:finish chain 1
INFO:cmdstanpy:start chain 3
INFO:cmdstanpy:start chain 4
INFO:cmdstanpy:finish chain 3
INFO:cmdstanpy:finish chain 4


alpha    1.318333
beta     4.978975
dtype: float64

In [200]:
k_ppc_gammalog = samples_gamma_post.posterior_predictive['k_ppc'].stack(
    {"sample": ("chain", "draw")}
).transpose("sample", "k_ppc_dim_0")

bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        k_ppc_gammalog,
        percentiles=[30, 50, 70, 99],
        data=data,
        x_axis_label='glucose binding rates (mM/hr)',
        title = 'Glucose Binding Rates as a Gamma Distribution'
    )
)

In [192]:
az.waic(samples_gamma_post)


Computed from 4000 by 30 log-likelihood matrix

          Estimate       SE
elpd_waic     8.85     5.13
p_waic        1.42        -

## Perform comparison

In [199]:
az.compare({'normal': samples_norm_postlog, 'gamma': samples_gamma_post}, ic='loo')

rank      loo    p_loo    d_loo       weight       se      dse warning  \
gamma     0  8.83641  1.43037        0     0.999542  3.97326        0   False   
normal    1 -1.67609  2.03026  10.5125  0.000458203  5.08773  2.43538   False   

       loo_scale  
gamma        log  
normal       log